In [1]:
import wandb
import math
import random
import torch, torchvision
import torch.nn as nn
import torchvision.transforms as T
import pickle
import pandas as pd
import geopandas as gpd

import gnn_io

from my_gnn import MyGNN

In [2]:
wandb.login()

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: enatterer (tum-traffic-engineering). Use `wandb login --relogin` to force relogin


True

In [3]:
# Load the dictionary
with open('../results/result_dic.pkl', 'rb') as f:
    results_dict = pickle.load(f)

datasets = []
for key, df in results_dict.items():
    print(f"Policy: {key}")
    
    if isinstance(df, pd.DataFrame):
        gdf = gpd.GeoDataFrame(df, geometry='geometry')
        gdf.crs = "EPSG:2154"  # Assuming the original CRS is EPSG:2154
        gdf.to_crs("EPSG:4326", inplace=True)
        edge_index, car_volume_tensor, policy_tensor, nodes = gnn_io.create_edge_index_and_tensors(gdf)
        datasets.append((policy_tensor, car_volume_tensor))
    else:
        print(f"The value for key '{key}' is not a GeoDataFrame.")

Policy: policy introduced in Arrondissement(s) 5, 6
Policy: policy introduced in Arrondissement(s) 1, 2, 3
Policy: policy introduced in Arrondissement(s) 3, 4
Policy: policy introduced in Arrondissement(s) 16, 17, 18
Policy: policy introduced in Arrondissement(s) 13, 14, 15
Policy: policy introduced in Arrondissement(s) 8, 9, 10, 11
Policy: policy introduced in Arrondissement(s) 12, 13
Policy: policy introduced in Arrondissement(s) 2, 3, 4, 5, 6, 7
Policy: policy introduced in Arrondissement(s) 9, 10, 11
Policy: policy introduced in Arrondissement(s) 15, 16, 17, 18, 19
Policy: policy introduced in Arrondissement(s) 7, 8, 9, 10, 11, 12
Policy: policy introduced in Arrondissement(s) 13, 14
Policy: policy introduced in Arrondissement(s) 2, 3, 4, 5, 6
Policy: policy introduced in Arrondissement(s) 5
Policy: policy introduced in Arrondissement(s) 2
Policy: policy introduced in Arrondissement(s) 11, 12, 13, 14
Policy: policy introduced in Arrondissement(s) 12, 13, 14, 15
Policy: policy intro

In [4]:
# max_value_total = 0
# mean_value_total = 0

# for policy_tensor, car_volume_tensor in datasets:
#     print(policy_tensor[:1])
#     print(car_volume_tensor[:1])
#     # Find the maximum and mean value of the car_volume_tensor
#     max_value = torch.max(car_volume_tensor)
#     mean_value = torch.mean(car_volume_tensor)
    
#     print(f"Max value of car_volume_tensor: {max_value.item()}")
#     print(f"Mean value of car_volume_tensor: {mean_value.item()}")
#     max_value_total = max(max_value_total, max_value)
#     mean_value_total = (mean_value_total + mean_value)/2
    
# print(max_value_total)
# print(mean_value_total)

In [5]:


def init_weights(m):
    if isinstance(m, nn.Linear):
        nn.init.kaiming_uniform_(m.weight, nonlinearity='relu')
        if m.bias is not None:
            nn.init.zeros_(m.bias)
            
gnn = MyGNN(policy_input_dim=3, traffic_input_dim=1, hidden_dim=8)
gnn.apply(init_weights)

MyGNN()

In [6]:
policy_input_dim = 3  # Dimensionality of policy features: capacity, freespeed flow, modes
traffic_input_dim = 1  # Dimensionality of traffic flow features
hidden_dim = 32  # Dimensionality of hidden representations
num_nodes = max(max(edge_index[0]), max(edge_index[1])) + 1  # Number of nodes in the graph

device = "cuda:0" if torch.cuda.is_available() else "cpu"

def get_dataloader(is_train, batch_size):
    loader = torch.utils.data.DataLoader(dataset=datasets, 
                                         batch_size=batch_size, 
                                         shuffle=True if is_train else False, 
                                         pin_memory=True, num_workers=2)
    return loader

# def normalize(tensor):
#     mean = tensor.mean(dim=0, keepdim=True)
#     std = tensor.std(dim=0, keepdim=True) + 1e-6  # Add a small epsilon to avoid division by zero
#     return (tensor - mean) / std

def min_max_normalize(tensor):
    min_val = tensor.min()
    max_val = tensor.max()
    normalized_tensor = (tensor - min_val) / (max_val - min_val)
    return normalized_tensor

def validate_model(model, valid_dl, loss_func):
    "Compute performance of the model on the validation dataset and log a wandb.Table"
    model.eval()
    val_loss = 0
    # correct = 0
    total = 0 
    with torch.inference_mode():
        # correct = 0
        total = 0  # Add a total counter for accuracy calculation

        for i, (policy_features, flow_targets) in enumerate(valid_dl):
             # Normalize data and labels
            policy_features = min_max_normalize(policy_features.float())  # Shape: [105, 31216, 3]
            flow_targets = min_max_normalize(flow_targets.float().unsqueeze(2)) # Shape: [105, 31216, 1]

            # Forward pass ➡
            outputs = gnn(edge_index, policy_features, flow_targets)
            print("flow targets: ", flow_targets[:1])
            print("outputs: ", outputs[:1])
            # Compute loss
            loss = loss_func(outputs, flow_targets)
            print(f"Loss: {loss.item()}")
            val_loss += loss.item() * flow_targets.size(0)  # Sum up the batch loss scaled by the number of examples
            print(f"Val loss: {val_loss}")
            total += flow_targets.size(0)  # Increment total by the number of labels
            
    average_val_loss = val_loss/total
    return average_val_loss  # Average loss over all examples, accuracy as correct predictions over total


In [7]:
# wandb.init(
#         project="my_project_diff_learning_rates",
#         config={
#             "epochs": 8,
#             "batch_size": 20,
#             "lr": 0.00001,
#     })

# config = wandb.config

# train_dl = get_dataloader(is_train=True, batch_size=config.batch_size)
# valid_dl = get_dataloader(is_train=False, batch_size=config.batch_size)

In [8]:
# for epoch in range(config.epochs):
#     print("epoch", epoch)
#     gnn.train()
#     # for step, (policy_features, flow_targets) in enumerate(train_dl): 
#     #     print("step", step)
#     #     print("policy_features", policy_features.shape)
    
#     print("valid dl", len(valid_dl.dataset))
#     validate_model(gnn, valid_dl, nn.MSELoss())
#     break

In [9]:
# fasdfsdf

In [14]:
# Launch 5 experiments, trying different dropout rates

learning_rates = [1e-3, 1e-2, 1e-1]  # List of learning rates to iterate over
# ,  1e-4, 1e-3, 1e-2, 1e-1
for lr in learning_rates:
    # 🐝 initialise a wandb run
    wandb.init(
        project="updated_gnn_5",
        config={
            "epochs": 20,
            "batch_size": 20,
            "lr": lr
    })
    
    # Copy your config 
    config = wandb.config

    # Get the data
    train_dl = get_dataloader(is_train=True, batch_size=config.batch_size)
    valid_dl = get_dataloader(is_train=False, batch_size=config.batch_size)
    n_steps_per_epoch = math.ceil(len(train_dl.dataset) / config.batch_size)
    
    # Make the loss and optimizer
    loss_func = nn.CrossEntropyLoss()
    optimizer = torch.optim.Adam(gnn.parameters(), lr=config.lr)

   # Training
    example_ct = 0
    step_ct = 0
    for epoch in range(config.epochs):
        print("epoch", epoch)
        gnn.train()
        for step, (policy_features, flow_targets) in enumerate(train_dl):            
            data, labels = min_max_normalize(policy_features.float()), min_max_normalize(flow_targets.float().unsqueeze(2))        
            outputs = gnn(edge_index, data, labels)
            print("Sample Policy Features: ", data[:5])
            print("Sample Traffic Features: ", labels[:5])
            print("Sample Flow Targets: ", outputs[:5])
            train_loss = loss_func(outputs, labels)
            optimizer.zero_grad()
            train_loss.backward()
            optimizer.step()
            example_ct += len(data)
            metrics = {"train/train_loss": train_loss, 
                       "train/epoch": (step + 1 + (n_steps_per_epoch * epoch)) / n_steps_per_epoch, 
                       "train/example_ct": example_ct}
            if step + 1 < n_steps_per_epoch:
                # 🐝 Log train metrics to wandb 
                wandb.log(metrics)
                
            step_ct += 1

        val_loss = validate_model(gnn, valid_dl, loss_func)

        # 🐝 Log train and validation metrics to wandb
        val_metrics = {"val/val_loss": val_loss}
        wandb.log({**metrics, **val_metrics})
        # print("Train loss", train_loss)
        # print("Valid loss", val_loss)
        # print("Accuracy", accuracy)
        # print(f"Train Loss: {train_loss:.3f}, Valid Loss: {val_loss:3f}, Accuracy: {accuracy:.2f}")

    # If you had a test set, this is how you could log it as a Summary metric
    wandb.summary['test_accuracy'] = 0.8

    # 🐝 Close your wandb run 
    wandb.finish()

epoch 0
Policy Hidden:  tensor([[[ 0.0540, -0.1504,  0.0614,  ...,  0.3337,  0.0934,  0.0723],
         [ 0.0540, -0.1504,  0.0614,  ...,  0.3337,  0.0934,  0.0723],
         [ 0.0540, -0.1504,  0.0614,  ...,  0.3337,  0.0934,  0.0723],
         ...,
         [ 0.0540, -0.1504,  0.0614,  ...,  0.3337,  0.0934,  0.0723],
         [ 0.0540, -0.1504,  0.0614,  ...,  0.3337,  0.0934,  0.0723],
         [ 0.0540, -0.1504,  0.0614,  ...,  0.3337,  0.0934,  0.0723]],

        [[ 0.0540, -0.1504,  0.0614,  ...,  0.3337,  0.0934,  0.0723],
         [ 0.0540, -0.1504,  0.0614,  ...,  0.3337,  0.0934,  0.0723],
         [ 0.0540, -0.1504,  0.0614,  ...,  0.3337,  0.0934,  0.0723],
         ...,
         [ 0.0540, -0.1504,  0.0614,  ...,  0.3337,  0.0934,  0.0723],
         [ 0.0540, -0.1504,  0.0614,  ...,  0.3337,  0.0934,  0.0723],
         [ 0.0540, -0.1504,  0.0614,  ...,  0.3337,  0.0934,  0.0723]],

        [[ 0.0540, -0.1504,  0.0614,  ...,  0.3337,  0.0934,  0.0723],
         [ 0.0540, -0

epoch 0
Policy Hidden:  tensor([[[ 0.0530, -0.1484,  0.0634,  ...,  0.3315,  0.0919,  0.0746],
         [ 0.0530, -0.1484,  0.0634,  ...,  0.3315,  0.0919,  0.0746],
         [ 0.0530, -0.1484,  0.0634,  ...,  0.3315,  0.0919,  0.0746],
         ...,
         [ 0.0530, -0.1484,  0.0634,  ...,  0.3315,  0.0919,  0.0746],
         [ 0.0530, -0.1484,  0.0634,  ...,  0.3315,  0.0919,  0.0746],
         [ 0.0530, -0.1484,  0.0634,  ...,  0.3315,  0.0919,  0.0746]],

        [[ 0.0530, -0.1484,  0.0634,  ...,  0.3315,  0.0919,  0.0746],
         [ 0.0530, -0.1484,  0.0634,  ...,  0.3315,  0.0919,  0.0746],
         [ 0.0530, -0.1484,  0.0634,  ...,  0.3315,  0.0919,  0.0746],
         ...,
         [ 0.0530, -0.1484,  0.0634,  ...,  0.3315,  0.0919,  0.0746],
         [ 0.0530, -0.1484,  0.0634,  ...,  0.3315,  0.0919,  0.0746],
         [ 0.0530, -0.1484,  0.0634,  ...,  0.3315,  0.0919,  0.0746]],

        [[ 0.0530, -0.1484,  0.0634,  ...,  0.3315,  0.0919,  0.0746],
         [ 0.0530, -0

epoch 0
Policy Hidden:  tensor([[[ 0.0693, -0.1469,  0.0025,  ...,  0.3237,  0.1086,  0.0277],
         [ 0.0693, -0.1469,  0.0025,  ...,  0.3237,  0.1086,  0.0277],
         [ 0.0693, -0.1469,  0.0025,  ...,  0.3237,  0.1086,  0.0277],
         ...,
         [ 0.0693, -0.1469,  0.0025,  ...,  0.3237,  0.1086,  0.0277],
         [ 0.0693, -0.1469,  0.0025,  ...,  0.3237,  0.1086,  0.0277],
         [ 0.0693, -0.1469,  0.0025,  ...,  0.3237,  0.1086,  0.0277]],

        [[ 0.0693, -0.1469,  0.0025,  ...,  0.3237,  0.1086,  0.0277],
         [ 0.0693, -0.1469,  0.0025,  ...,  0.3237,  0.1086,  0.0277],
         [ 0.0693, -0.1469,  0.0025,  ...,  0.3237,  0.1086,  0.0277],
         ...,
         [ 0.0693, -0.1469,  0.0025,  ...,  0.3237,  0.1086,  0.0277],
         [ 0.0693, -0.1469,  0.0025,  ...,  0.3237,  0.1086,  0.0277],
         [ 0.0693, -0.1469,  0.0025,  ...,  0.3237,  0.1086,  0.0277]],

        [[ 0.0693, -0.1469,  0.0025,  ...,  0.3237,  0.1086,  0.0277],
         [ 0.0693, -0